 <!-- ![Exercise Header](https://.jpg) -->

### Pre-Requisites

In [ ]:
#!pip install folium
#!pip install gpxpy

In [2]:
import gpxpy
import gpxpy.gpx

import pandas as pd

import folium

# GPX Version

### Load and Display Different Routes 
- PyLoadRoutes
- PyDisplayRoutes

**Powered by Folium and OpenStreetMaps**

In [3]:
route_map = folium.Map(
    location=[47, 32.5],
    zoom_start=5,
    tiles='OpenStreetMap',
    # width=924,
    # height=600
    width=800,
    height=450
)

In [4]:
def PyLoadRoutes(your_route_map,route_path,hex_color):
    
    print(f"Loading the GPX files at: {route_path}")

    with open(route_path, 'r') as gpx_file:
        gpx = gpxpy.parse(gpx_file)

    route_info = []

    for track in gpx.tracks:
        for segment in track.segments:
            for point in segment.points:
                route_info.append({
                    'latitude': point.latitude,
                    'longitude': point.longitude,
                    'elevation': point.elevation
                })

    route_df = pd.DataFrame(route_info)

    coordinates = [tuple(x) for x in route_df[['latitude', 'longitude']].to_numpy()]
    folium.PolyLine(coordinates, weight=3,color=hex_color).add_to(route_map)
    folium.LayerControl().add_to(route_map)

    #if you want to display/save after adding every path separately:
    #display(route_map)
    #route_map.save('./output_map.html')

    


In [5]:
PyLoadRoutes(route_map,'My_Routes/PL-SK-HU.gpx','#119403')
route_map.save('./Output_map_PL-SK-HU.html')
display(route_map)

Loading the GPX files at: My_Routes/PL-SK-HU.gpx


In [117]:
PyLoadRoutes(route_map,'My_Routes/PL-SK-HU.gpx','green')
PyLoadRoutes(route_map,'HU-GR_gpx/HU-GR.gpx','#808080')

#if you want to display/save the combined map to visualize all routes together:
display(route_map)
#route_map.save('./output_map.html')

Loading the GPX files at: My_Routes/PL-SK-HU.gpx
Loading the GPX files at: HU-GR_gpx/HU-GR.gpx


## Displaying: Altitude & Distance

In [ ]:
# !pip install haversine

In [5]:
# PyLoadRoutes(route_map,'My_Routes/PL-SK-HU.gpx','green')


# #if you want to display/save the combined map to visualize all routes together:
# display(route_map)
# #route_map.save('./output_map.html')

In [6]:
#with open('Polar_Data/Polar_Route.GPX', 'r') as gpx_file:
with open('My_Routes/PL-SK-HU.gpx', 'r') as gpx_file:
    gpx = gpxpy.parse(gpx_file)

In [7]:
gpx.get_track_points_no()

31645

In [8]:
gpx.get_elevation_extremes()

MinimumMaximum(minimum=130.615291, maximum=966.654872)

In [9]:
route_info = []

for track in gpx.tracks:
    for segment in track.segments:
        for point in segment.points:
            route_info.append({
                'latitude': point.latitude,
                'longitude': point.longitude,
                'elevation': point.elevation
            })

route_df = pd.DataFrame(route_info)
route_df.head()

latitude  longitude   elevation
0  49.864104  19.109029  386.362446
1  49.864275  19.109137  386.362446
2  49.864374  19.109211  386.362446
3  49.864470  19.109280  386.362446
4  49.864582  19.109354  386.362446

In [10]:
import haversine as hs

def haversine_distance(lat1, lon1, lat2, lon2) -> float:
    distance = hs.haversine(
        point1=(lat1, lon1),
        point2=(lat2, lon2),
        unit=hs.Unit.METERS
    )
    return np.round(distance, 2)

import numpy as np


haversine_distance(
    lat1=route_df.iloc[0]['latitude'],
    lon1=route_df.iloc[0]['longitude'],
    lat2=route_df.iloc[1]['latitude'],
    lon2=route_df.iloc[1]['longitude']
)

20.53

In [11]:
distances = [np.nan]

for i in range(len(route_df)):
    if i == 0:
        continue
    else:
        distances.append(haversine_distance(
            lat1=route_df.iloc[i - 1]['latitude'],
            lon1=route_df.iloc[i - 1]['longitude'],
            lat2=route_df.iloc[i]['latitude'],
            lon2=route_df.iloc[i]['longitude']
        ))
        
route_df['distance'] = distances
route_df.head()

latitude  longitude   elevation  distance
0  49.864104  19.109029  386.362446       NaN
1  49.864275  19.109137  386.362446     20.53
2  49.864374  19.109211  386.362446     12.22
3  49.864470  19.109280  386.362446     11.76
4  49.864582  19.109354  386.362446     13.54

In [12]:
print(route_df['distance'].sum())

route_df['elevation_diff'] = route_df['elevation'].diff()

#route_df['cum_elevation'] = route_df['elevation_diff'].cumsum()


#make elevation_diff zero if it is negative
route_df['cum_elevation'] = route_df['elevation_diff'].where(route_df['elevation_diff'] > 0, 0).cumsum()  #m


route_df['cum_distance'] = route_df['distance'].cumsum()/1000 #km

route_df = route_df.fillna(0)

#index to column
route_df.reset_index(inplace=True)

route_df.head()



403980.26


index   latitude  longitude   elevation  distance  elevation_diff  \
0      0  49.864104  19.109029  386.362446      0.00             0.0   
1      1  49.864275  19.109137  386.362446     20.53             0.0   
2      2  49.864374  19.109211  386.362446     12.22             0.0   
3      3  49.864470  19.109280  386.362446     11.76             0.0   
4      4  49.864582  19.109354  386.362446     13.54             0.0   

   cum_elevation  cum_distance  
0            0.0       0.00000  
1            0.0       0.02053  
2            0.0       0.03275  
3            0.0       0.04451  
4            0.0       0.05805

In [13]:
import plotly.express as px

fig = px.line(route_df, x='cum_distance', y='elevation',
              color_discrete_sequence=['#30b854'])


fig.update_layout(
    title={
        'text': "Elevation Profile",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis=dict(
        title="Distance (km)"
    ),
    yaxis=dict(
        title="Meters"
    ))


fig.show()

In [32]:
fig.write_html("./Output_Elevation_Profile.html")

In [33]:
import plotly.express as px

fig = px.line(route_df, x='cum_distance', y='cum_elevation',
              color_discrete_sequence=['#30b854'])

fig.update_layout(
    title={
        'text': "Cumulative Height",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis=dict(
        title="Distance (km)"
    ),
    yaxis=dict(
        title="Cumulative Height (m)"
    ))


fig.show()

In [34]:
fig.write_html("./Output_Cumulative_Elevation.html")

In [44]:
import plotly.figure_factory as ff
from scipy.stats import norm
import numpy as np
np.random.seed(123)

data = route_df['elevation_diff'].tolist() #np.random.noncentral_chisquare(3, 20, 1000)

m, s = norm.fit(data)
gaussian_data = np.random.normal(m, s, 10000)

fig = ff.create_distplot(
    [data, gaussian_data],
    group_labels=["% Slope Distribution", f"Gaussian: m={m:.2f}, s={s:.2f}"],
    curve_type="kde", show_rug=False
)

fig.update_layout(
    title={
        'text': "Distribution Plot",
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis=dict(
        title="% Slope"
    ),
    yaxis=dict(
        title="Y"
    ))


fig.show()

In [86]:
#creating a conditional column on route_df based on elevation_diff:

route_df['slope'] = np.where(route_df['elevation_diff'] > 0, 1, -1)

route_df['slope_str'] = np.where(route_df['elevation_diff'] > 0, "Up", "Down")


0       -1
1       -1
2       -1
3       -1
4       -1
        ..
31640   -1
31641   -1
31642   -1
31643   -1
31644   -1
Name: slope, Length: 31645, dtype: int32

In [63]:
route_df.head(5)

index   latitude  longitude   elevation  distance  elevation_diff  \
0      0  49.864104  19.109029  386.362446      0.00             0.0   
1      1  49.864275  19.109137  386.362446     20.53             0.0   
2      2  49.864374  19.109211  386.362446     12.22             0.0   
3      3  49.864470  19.109280  386.362446     11.76             0.0   
4      4  49.864582  19.109354  386.362446     13.54             0.0   

   cum_elevation  cum_distance  slope slope_str  
0            0.0       0.00000     -1      Down  
1            0.0       0.02053     -1      Down  
2            0.0       0.03275     -1      Down  
3            0.0       0.04451     -1      Down  
4            0.0       0.05805     -1      Down

In [109]:
#first ocurrance of Down in column slope_str
first_up_idx = route_df.slope_str.ne('Up').idxmin()
first_down_idx = route_df.slope_str.ne('Down').idxmin()


a=route_df #.head(2000)

a["showlegend"] = False
showlegendIdx = a.columns.get_indexer(["showlegend"])[0]

a.iat[first_up_idx, showlegendIdx] = True
a.iat[first_down_idx, showlegendIdx] = True

a["showlegend"] = a["showlegend"].astype(object)


In [1]:
import numpy as np
import pandas as pd
from datetime import datetime
import plotly.express as px
import plotly.graph_objects as go



fig = go.Figure(
    [
        go.Scatter(
            #x = a.index[tn : tn + 2],
            x = a['cum_distance'][tn : tn + 2],
            y = a['elevation'][tn : tn + 2],
            mode='lines+markers',
            #mode='lines',
            # line_shape="hv",
            line_color=px.colors.qualitative.Plotly[route_df['slope'][tn]],
            name=a['slope_str'][tn],
            legendgroup= a['slope_str'][tn],
            showlegend= a['showlegend'][tn],
        )
        for tn in range(len(a))
    ]
)

fig.update_layout(legend_title_text='Climbing or Descending')

fig.update_layout(
    title={
        'text': "Elevation Profile",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'},
    xaxis=dict(
        title="Distance (km)"
    ),
    yaxis=dict(
        title="Meters"
    ))


#fig.show()

In [112]:
fig.write_html("./Output_Elevation_Profile_UpDown.html")